# Time Series to observe HOURLY temperature variations 
## Hourly temperature prediction using KERAS

In [1]:
import warnings 
warnings.filterwarnings('ignore')

In [2]:
import numpy as np
import pandas as pd

import seaborn as sns
import matplotlib as mpl
import matplotlib.pyplot as plt

import plotly
from plotly.offline import plot, iplot , plot_mpl, init_notebook_mode
# Make plotly work with Jupyter notebook
import cufflinks as cf
import plotly.graph_objs as go

mpl.style.use('seaborn')
init_notebook_mode(connected=True)

/anaconda3/lib/python3.6/site-packages/plotly/graph_objs/_deprecations.py:558: DeprecationWarning:

plotly.graph_objs.YAxis is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.layout.YAxis
  - plotly.graph_objs.layout.scene.YAxis


/anaconda3/lib/python3.6/site-packages/plotly/graph_objs/_deprecations.py:531: DeprecationWarning:

plotly.graph_objs.XAxis is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.layout.XAxis
  - plotly.graph_objs.layout.scene.XAxis




In [3]:
from keras.models import Sequential, Model
from keras.layers import Input, Dense, Activation
from keras.optimizers import Adam
from sklearn.metrics import mean_squared_error

Using TensorFlow backend.


In [4]:
X_train = pd.read_pickle('./X_train_hourly.pkl')
Y_train = pd.read_pickle('./Y_train_hourly.pkl')

X_test  = pd.read_pickle('./X_test_hourly.pkl')
Y_test  = pd.read_pickle('./Y_test_hourly.pkl')


print("Shape of Training Dataset " , X_train.shape)
print("Shape of Testing Dataset " , X_test.shape)

X_train.head()

Shape of Training Dataset  (43813, 9)
Shape of Testing Dataset  (1440, 9)


month  day  hour   day_sin   day_cos  month_sin  \
datetime                                                               
2012-10-01 12:00:00     10    1    12  0.017213  0.999852  -0.866025   
2012-10-01 13:00:00     10    1    13  0.017213  0.999852  -0.866025   
2012-10-01 14:00:00     10    1    14  0.017213  0.999852  -0.866025   
2012-10-01 15:00:00     10    1    15  0.017213  0.999852  -0.866025   
2012-10-01 16:00:00     10    1    16  0.017213  0.999852  -0.866025   

                     month_cos  hour_sin  hour_cos  
datetime                                            
2012-10-01 12:00:00        0.5 -0.136167 -0.990686  
2012-10-01 13:00:00        0.5 -0.398401 -0.917211  
2012-10-01 14:00:00        0.5 -0.631088 -0.775711  
2012-10-01 15:00:00        0.5 -0.816970 -0.576680  
2012-10-01 16:00:00        0.5 -0.942261 -0.334880

In [5]:
def train_model(X_train, y_train, X_test, y_test, epochs):
    model = Sequential(
        [
            Dense(10, activation="relu", input_shape=(X_train.shape[1],)),
            Dense(10, activation="relu"),
            Dense(10, activation="relu"),
            Dense(1, activation="linear")
        ]
    )
    model.compile(optimizer=Adam(), loss="mean_squared_error")
    
    history = model.fit(X_train, y_train, epochs=epochs,shuffle=False)
    return model, history

In [6]:
model_encoded, encoded_hist = train_model(
    X_train,
    Y_train,
    X_test,
    Y_test,
    epochs=50
)

Epoch 1/50
43813/43813 [==============================] - 1s 34us/step - loss: 35.9162
Epoch 2/50
43813/43813 [==============================] - 1s 25us/step - loss: 16.9693
Epoch 3/50
43813/43813 [==============================] - 1s 25us/step - loss: 16.4138
Epoch 4/50
43813/43813 [==============================] - 1s 26us/step - loss: 16.0424
Epoch 5/50
43813/43813 [==============================] - 1s 25us/step - loss: 15.6493
Epoch 6/50
43813/43813 [==============================] - 1s 25us/step - loss: 15.2689
Epoch 7/50
43813/43813 [==============================] - 1s 24us/step - loss: 14.9599
Epoch 8/50
43813/43813 [==============================] - 1s 26us/step - loss: 14.6717
Epoch 9/50
43813/43813 [==============================] - 1s 25us/step - loss: 14.4117
Epoch 10/50
43813/43813 [==============================] - 1s 25us/step - loss: 14.1467
Epoch 11/50
43813/43813 [==============================] - 1s 25us/step - loss: 13.9053
Epoch 12/50
43813/43813 [================

In [8]:
Y_test_pred = model_encoded.predict(X_test)
mse_encoded = mean_squared_error(Y_test, model_encoded.predict(X_test))
print(mse_encoded)

future_forecast = pd.DataFrame(Y_test_pred,index = Y_test.index,columns=['Prediction'])
predictions = pd.concat([Y_test,future_forecast],axis=1)
predictions.head(10)

21.0038418043


temperature  Prediction
datetime                                    
2017-10-01 01:00:00        24.29   24.854595
2017-10-01 02:00:00        22.48   23.477095
2017-10-01 03:00:00        20.56   22.312065
2017-10-01 04:00:00        20.06   21.174198
2017-10-01 05:00:00        19.00   20.001072
2017-10-01 06:00:00        19.00   18.669981
2017-10-01 07:00:00        19.16   17.781061
2017-10-01 08:00:00        19.00   17.023115
2017-10-01 09:00:00        18.76   16.477150
2017-10-01 10:00:00        18.46   16.017366

In [9]:
iplot([{
    'x': predictions.index,
    'y': predictions[col],
    'name': col
}  for col in predictions.columns], filename='cufflinks/simple-line')

In [10]:
fig = go.Figure(data=[{
    'x': X_train.index,
    'y': Y_train["temperature"],
    'name': "train temperature"
},{
    'x': X_test.index,
    'y': Y_test["temperature"],
    'name': "test temperature"
},{
    'x': future_forecast.index,
    'y': future_forecast["Prediction"],
    'name': "Predicted temperature"
}])


iplot(fig, filename='cufflinks/simple-line')